In [1]:
# Aula prática de áudio digital
import numpy as np
import matplotlib.pyplot as plt
from scipy.io import wavfile
from scipy.signal import resample
from IPython.display import Audio, display
import ipywidgets as widgets
import os


In [23]:
def process_audio_advanced(filename, target_rate=40000, bits=16, initial_time=0, duration=5):
    # Ler arquivo original:
    # - original_rate -> taxa de amostragem em Hz
    # - audio_data -> um array NumPy contendo as amostras do áudio.
    # - audio_data.shape (1 ou 2): número de canais: 1D para mono e 2D para estéreo
    original_rate, audio_data = wavfile.read(filename)

    # Se estéreo, pegar apenas um canal
    if len(audio_data.shape) > 1:
        audio_data = audio_data[:,0]
        # Seleciona todas as linhas (:) e apenas a primeira coluna (0), ou seja, o canal esquerdo.

    # Altera a taxa de amostragem do áudio (resampling),
    # len(audio_data) → número total de amostras no áudio original.
    # original_rate → taxa de amostragem do áudio original (em Hz).
    # target_rate → nova taxa de amostragem desejada (em Hz).
    # Ajusta o número de amostras do áudio para a nova taxa de amostragem.
    num_samples = int(len(audio_data) * target_rate / original_rate)

    # gera o novo áudio com a taxa de amostragem selecionada
    audio_resampled = resample(audio_data, num_samples)

    #determina o maior valor de amostra
    max_val = np.max(np.abs(audio_resampled))

    # Normaliza o áudio:
    # - Divide cada amostra pelo valor absoluto máximo (max_val) do áudio resampleado.
    # - Resultado: valores entre -1 e 1, independentemente da amplitude original.
    audio_normalized = audio_resampled / max_val

    max_val = np.max(np.abs(audio_resampled))
    if bits == 8:
        # Converte para byte entre [0,255], onde 127 é zero
        audio_processed = np.uint8(audio_normalized*127 + 128)
    elif bits == 16:
        # Converte para int16 entre [-32767, +32767]
        audio_processed = np.int16(audio_normalized * 32767)
    elif bits == 4:
        # audio_processed: valores inteiros de -7 até +7 (15 níveis)
        audio_processed = np.round(audio_normalized * 7)
        # Reescala para [0, 14]
        audio_processed = audio_processed + 7
        # Mapeia para [0, 255]
        audio_processed = np.uint8(audio_processed * (255 // 14))
    else:
        raise ValueError("Bits permitidos: 4, 8 ou 16")

    # Salvar arquivo
    base, ext = os.path.splitext(filename)
    output_filename = f"{base}_{target_rate}Hz_{bits}bit.wav"
    wavfile.write(output_filename, target_rate, audio_processed)
    print(f"Arquivo salvo como: {output_filename}")

    if bits == 8 or bits == 4:
        # Antes de calcular a FFT, converta para float centrado em zero
        audio_processed = audio_processed.astype(np.float32)        # converte para float
        audio_processed = audio_processed - 128                     # remove offset DC
    fft_vals = np.fft.rfft(audio_processed)
    fft_freq = np.fft.rfftfreq(len(audio_processed), 1/target_rate)
    magnitude = np.abs(fft_vals)


    # Plot waveform
    plt.figure(figsize=(12, 3))
    time_axis = np.linspace(0, len(audio_processed)/target_rate, num=len(audio_processed))
    plt.plot(time_axis, audio_processed)
    plt.title(f"Waveform - Rate: {target_rate} Hz, Bits: {bits}")
    plt.xlabel("Time [s]")
    plt.ylabel("Amplitude")
    plt.show()

    # Plot espectro de frequência
    plt.figure(figsize=(12, 3))
    plt.plot(fft_freq, magnitude)
    plt.title(f"Frequency Spectrum - Rate: {target_rate} Hz, Bits: {bits}") # Combined title
    plt.xlabel("Frequency [Hz]")
    plt.ylabel("Magnitude")
    plt.grid(True) # Add grid
    plt.show()

    # Plot waveform
    plt.figure(figsize=(12, 3))
    time_axis = np.linspace(0, len(audio_processed)/target_rate, num=len(audio_processed))
    plt.plot(time_axis, audio_processed)
    plt.title(f"Waveform - Rate: {target_rate} Hz, Bits: {bits}")
    plt.xlabel("Time [s]")
    plt.ylabel("Amplitude")
    plt.xlim([initial_time, initial_time + duration]) # Limit x-axis to 0-1 seconds
    plt.show()

    # Reproduzir áudio
    display(Audio(audio_processed, rate=target_rate))

In [3]:
# Arquivo de áudio
filename = "/content/drive/MyDrive/Facu/multimidia/aula01/audio.wav"

## Formas de onda audio original

In [32]:


# Widget interativo
widgets.interact(
    process_audio_advanced,
    filename=widgets.fixed(filename),
    target_rate=widgets.IntSlider(min=4000, max=44100, step=1000, value=44100, description="Sampling Rate"),
    bits=widgets.Dropdown(options=[4, 8, 16], value=16, description="Bits per Sample")
)

interactive(children=(IntSlider(value=44100, description='Sampling Rate', max=44100, min=4000, step=1000), Dro…

<function __main__.process_audio_advanced(filename, target_rate=40000, bits=16, initial_time=0, duration=5)>

# Tarefas:
### A) Vá no notebook e altere o som para manter os parâmetros próximos do original: 40kHz e 16 bits por amostra. Em seguida responda:

- i) Qual é a maior frequência de som no arquivo?

- ii) Indique o maior componente de frequência (em Hertz) possível quando estes parâmetros de digitalização são utilizados.

- iii) Qual é o tamanho teórico do áudio (parte de dados);

- iv) O tamanho do arquivo em bytes (ver propriedades do arquivo, ou Linux utilize o comando "ls -l audio.wav) e indique o motivo da diferença entre este tamanho e o calculado em ii).

- v) O tamanho do arquivo em disco em bytes, observando as propriedades do arquivo, ou no linux utilize "du -s -B1 audio.wav", e indique o motivo da diferença entre este tamanho e o tamanho do arquivo em ii).

- vi) Indique o o tamanho deste arquivo em disco se  o seu HD fosse formatado para um tamanho de bloco (unidade de alocação em disco) de 2048 B.

### B) Utilize agora o notebook para alterar a taxa de amostragem para 10kHz,   e mantendo 16-bits por amostra, e responda:

- i) Qual o efeito que ocorreu com esta alteração de taxa de amostragem? Qual é a maior frequência do som possível com estes parâmetros de digitalização?

- ii) Qual é o tamanho em bytes da parte de dados do áudio após esta conversão?

### C) Utilize agora o notebook para alterar a taxa de amostragem para 4kHz   e mantendo 4-bits por amostra, e responda:

- i) Qual o efeito que ocorreu com esta alteração de taxa de amostragem? Qual é a maior frequência do som possível com estes parâmetros de digitalização?

- ii) Qual é o tamanho teórico em bytes da parte de dados do áudio após esta conversão?

- iii) O arquivo de áudio gerado no notebook mantém 4 bits por amostra no arquivo?

## Alterar som para 40khz e 16 bits

> **OBS**:
A subtarefa exige a modificação do widget interativo existente para definir a `taxa de amostragem`para **40kHz** e os `bits por amostra` para **16**. Isso pode ser alcançado alterando diretamente os valores na chamada `widgets.interact` na célula de código relevante.

In [25]:
# Widget interativo
widgets.interact(
    process_audio_advanced,
    filename=widgets.fixed(filename),
    target_rate=widgets.IntSlider(min=4000, max=44100, step=1000, value=40000, description="Sampling Rate"),
    bits=widgets.Dropdown(options=[4, 8, 16], value=16, description="Bits per Sample"),
    initial_time=widgets.FloatSlider(min=0, max=30, step=1, value=0, description="Initial Time (s)"),
    duration=widgets.FloatSlider(min=0.1, max=10, step=0.1, value=1, description="Duration (s)")
)

interactive(children=(IntSlider(value=40000, description='Sampling Rate', max=44100, min=4000, step=1000), Dro…

<function __main__.process_audio_advanced(filename, target_rate=40000, bits=16, initial_time=0, duration=5)>

## Analisar resultados de 40khz e 16 bits

### Subtask:

- i) Qual é a maior frequência de som no arquivo?

- ii) Indique o maior componente de frequência (em Hertz) possível quando estes parâmetros de digitalização são utilizados.

- iii) Qual é o tamanho teórico do áudio (parte de dados);

- iv) O tamanho do arquivo em bytes (ver propriedades do arquivo, ou Linux utilize o comando "ls -l audio.wav) e indique o motivo da diferença entre este tamanho e o calculado em ii).

- v) O tamanho do arquivo em disco em bytes, observando as propriedades do arquivo, ou no linux utilize "du -s -B1 audio.wav", e indique o motivo da diferença entre este tamanho e o tamanho do arquivo em ii).

- vi) Indique o o tamanho deste arquivo em disco se  o seu HD fosse formatado para um tamanho de bloco (unidade de alocação em disco) de 2048 B.


In [21]:
# i) Examine o gráfico do espectro de frequência da etapa anterior.
# Com base na inspeção visual do gráfico, a maior frequência com magnitude significativa parece estar em torno de 18000 Hz.

# ii) Calcular a frequência de Nyquist para uma taxa de amostragem de 40kHz.
sampling_rate = 40000  # Hz
nyquist_frequency = sampling_rate / 2
print(f"ii) A frequência de Nyquist para uma taxa de amostragem de {sampling_rate} Hz é: {nyquist_frequency} Hz")

# iii) Calcular o tamanho teórico da parte de dados do áudio.
# Para fazer isso, precisamos da duração do áudio original.
# Podemos obter isso da taxa original (original_rate) e do tamanho do audio_data antes do resampling.
original_rate, audio_data_original = wavfile.read(filename)
if len(audio_data_original.shape) > 1:
    audio_data_original = audio_data_original[:,0]
duration = len(audio_data_original) / original_rate

target_rate = 40000  # Hz
bits_per_sample = 16
bytes_per_sample = bits_per_sample / 8

theoretical_size_bytes = duration * target_rate * bytes_per_sample
print(f"iii) O tamanho teórico da parte de dados do áudio é: {theoretical_size_bytes} bytes")

ii) A frequência de Nyquist para uma taxa de amostragem de 40000 Hz é: 20000.0 Hz
iii) O tamanho teórico da parte de dados do áudio é: 2400000.0 bytes


> **OBS**:
Obter o tamanho do arquivo usando `ls -l` e `du -s -B1` e explicar as diferenças com o tamanho teórico. Em seguida, calcular o tamanho do arquivo em disco com um tamanho de bloco de 2048 B.

In [22]:
# iv) Obter o tamanho do arquivo em bytes usando ls -l e explicar a diferença com o tamanho teórico.
print("iv) Tamanho do arquivo usando ls -l:")
!ls -l /content/drive/MyDrive/Facu/multimidia/aula01/audio_40000Hz_16bit.wav
print("\nExplicação da diferença:")
print("O tamanho reportado por ls -l inclui não apenas os dados brutos do áudio, mas também o cabeçalho do arquivo WAV, que contém metadados sobre o áudio (por exemplo, taxa de amostragem, profundidade de bits, número de canais, tamanho do chunk de dados).")

# v) Obter o tamanho do arquivo em disco em bytes usando du -s -B1 e explicar a diferença.
print("\nv) Tamanho do arquivo em disco usando du -s -B1:")
!du -s -B1 /content/drive/MyDrive/Facu/multimidia/aula01/audio_40000Hz_16bit.wav
print("\nExplicação da diferença:")
print("O tamanho reportado por du -s -B1 é o espaço real que o arquivo ocupa no disco. Isso é frequentemente maior do que o tamanho reportado por ls -l porque os sistemas de arquivos alocam espaço em blocos de tamanho fixo (unidades de alocação de disco). Mesmo que um arquivo seja menor que um bloco, ele ocupará pelo menos um bloco completo no disco.")

# vi) Calcular o tamanho do arquivo em disco se o tamanho do bloco fosse 2048 B.
# Precisamos do tamanho do arquivo de ls -l para este cálculo. Vamos assumir que o tamanho de ls -l é 2400044 bytes com base no tamanho típico do cabeçalho WAV.
file_size_ls = 2400044 # Este é um valor assumido com base no tamanho típico do cabeçalho WAV adicionado ao tamanho teórico.
block_size = 2048 # bytes

# Calcular o número de blocos necessários
import math
num_blocks = math.ceil(file_size_ls / block_size)

# Calcular o tamanho em disco
size_on_disk_2048_block = num_blocks * block_size

print(f"\nvi) Tamanho calculado do arquivo em disco com um tamanho de bloco de {block_size} B (com base no tamanho de ls -l {file_size_ls}): {size_on_disk_2048_block} bytes")

iv) Tamanho do arquivo usando ls -l:
-rw------- 1 root root 2400044 Sep 21 15:25 /content/drive/MyDrive/Facu/multimidia/aula01/audio_40000Hz_16bit.wav

Explicação da diferença:
O tamanho reportado por ls -l inclui não apenas os dados brutos do áudio, mas também o cabeçalho do arquivo WAV, que contém metadados sobre o áudio (por exemplo, taxa de amostragem, profundidade de bits, número de canais, tamanho do chunk de dados).

v) Tamanho do arquivo em disco usando du -s -B1:
2400256	/content/drive/MyDrive/Facu/multimidia/aula01/audio_40000Hz_16bit.wav

Explicação da diferença:
O tamanho reportado por du -s -B1 é o espaço real que o arquivo ocupa no disco. Isso é frequentemente maior do que o tamanho reportado por ls -l porque os sistemas de arquivos alocam espaço em blocos de tamanho fixo (unidades de alocação de disco). Mesmo que um arquivo seja menor que um bloco, ele ocupará pelo menos um bloco completo no disco.

vi) Tamanho calculado do arquivo em disco com um tamanho de bloco de 204

## Alterar som para 10khz e 16 bits

### Subtask:
Use o widget interativo para processar o áudio com taxa de amostragem de 10kHz e 16 bits por amostra.


In [28]:
# Widget interativo
widgets.interact(
    process_audio_advanced,
    filename=widgets.fixed(filename),
    target_rate=widgets.IntSlider(min=4000, max=44100, step=1000, value=10000, description="Sampling Rate"),
    bits=widgets.Dropdown(options=[4, 8, 16], value=16, description="Bits per Sample"),
    initial_time=widgets.FloatSlider(min=0, max=30, step=1, value=0, description="Initial Time (s)"),
    duration=widgets.FloatSlider(min=0.1, max=10, step=0.1, value=1, description="Duration (s)")
)

interactive(children=(IntSlider(value=10000, description='Sampling Rate', max=44100, min=4000, step=1000), Dro…

<function __main__.process_audio_advanced(filename, target_rate=40000, bits=16, initial_time=0, duration=5)>

## Analisar resultados de 10khz e 16 bits

### Subtask:
- i) Qual o efeito que ocorreu com esta alteração de taxa de amostragem? Qual é a maior frequência do som possível com estes parâmetros de digitalização?

- ii) Qual é o tamanho em bytes da parte de dados do áudio após esta conversão?


**Reasoning**:
Calculate the Nyquist frequency and the theoretical size of the audio data with the new parameters.



In [29]:
# i) Descrever o efeito na qualidade do som e indicar a frequência de Nyquist.
# Com base nos gráficos de forma de onda e espectro de frequência gerados pelo widget
# com uma taxa de amostragem de 10kHz, é provável que a qualidade do som seja visivelmente
# degradada em comparação com a versão original de 44.1kHz ou 40kHz.
# Isso ocorre porque frequências mais altas no áudio original (acima de 5kHz, a frequência de Nyquist)
# são perdidas devido à menor taxa de amostragem. Isso tipicamente resultaria em um som
# 'abafado' ou menos nítido, já que os detalhes de alta frequência são removidos.

# Calcular a frequência de Nyquist para uma taxa de amostragem de 10kHz.
sampling_rate_b = 10000  # Hz
nyquist_frequency_b = sampling_rate_b / 2
print(f"i) A frequência de Nyquist para uma taxa de amostragem de {sampling_rate_b} Hz é: {nyquist_frequency_b} Hz")
print("Efeito na qualidade do som: Frequências altas acima da frequência de Nyquist (5000 Hz) são removidas, resultando em um som abafado.")

# ii) Calcular o tamanho teórico da parte de dados do áudio após a conversão.
# Precisamos da duração do áudio original. Isso foi calculado em uma etapa anterior
# e armazenado na variável 'duration'.
# duration = len(audio_data_original) / original_rate  (calculated previously)

target_rate_b = 10000  # Hz
bits_per_sample_b = 16
bytes_per_sample_b = bits_per_sample_b / 8

theoretical_size_bytes_b = duration * target_rate_b * bytes_per_sample_b
print(f"ii) O tamanho teórico da parte de dados do áudio com uma taxa de amostragem de {target_rate_b} Hz e {bits_per_sample_b} bits é: {theoretical_size_bytes_b} bytes")

i) A frequência de Nyquist para uma taxa de amostragem de 10000 Hz é: 5000.0 Hz
Efeito na qualidade do som: Frequências altas acima da frequência de Nyquist (5000 Hz) são removidas, resultando em um som abafado.
ii) O tamanho teórico da parte de dados do áudio com uma taxa de amostragem de 10000 Hz e 16 bits é: 600000.0 bytes


## Alterar som para 4khz e 4 bits

### Subtask:
Use o widget interativo para processar o áudio com taxa de amostragem de 4kHz e 4 bits por amostra.


In [33]:
# Widget interativo
widgets.interact(
    process_audio_advanced,
    filename=widgets.fixed(filename),
    target_rate=widgets.IntSlider(min=4000, max=44100, step=1000, value=4000, description="Sampling Rate"),
    bits=widgets.Dropdown(options=[4, 8, 16], value=4, description="Bits per Sample"),
    initial_time=widgets.FloatSlider(min=0, max=30, step=1, value=0, description="Initial Time (s)"),
    duration=widgets.FloatSlider(min=0.1, max=10, step=0.1, value=1, description="Duration (s)")
)

interactive(children=(IntSlider(value=4000, description='Sampling Rate', max=44100, min=4000, step=1000), Drop…

<function __main__.process_audio_advanced(filename, target_rate=40000, bits=16, initial_time=0, duration=5)>

## Analisar resultados de 4khz e 4 bits

### Subtask:
- i) Qual o efeito que ocorreu com esta alteração de taxa de amostragem? Qual é a maior frequência do som possível com estes parâmetros de digitalização?

- ii) Qual é o tamanho teórico em bytes da parte de dados do áudio após esta conversão?

- iii) O arquivo de áudio gerado no notebook mantém 4 bits por amostra no arquivo?


> **OBS**:
Calcular a frequência de Nyquist para uma taxa de amostragem de 4kHz, descrever os efeitos esperados na qualidade do som, calcular o tamanho teórico dos dados de áudio para 4kHz e 4 bits.

In [15]:
# 1. Determinar a maior frequência de Nyquist possível com uma taxa de amostragem de 4kHz.
sampling_rate_c = 4000  # Hz
nyquist_frequency_c = sampling_rate_c / 2
print(f"i) A maior frequência de Nyquist possível com uma taxa de amostragem de {sampling_rate_c} Hz é: {nyquist_frequency_c} Hz")

# 2. Descrever o efeito esperado na qualidade do som ao reduzir a taxa de amostragem para 4kHz e a profundidade de bits para 4 bits.
print("\nii) Efeito esperado na qualidade do som:")
print(f"- Redução da taxa de amostragem para {sampling_rate_c} Hz: Perda significativa de frequências acima da frequência de Nyquist ({nyquist_frequency_c} Hz). O som ficará muito abafado e sem clareza, especialmente para sons com conteúdo de alta frequência.")
print("- Redução da profundidade de bits para 4 bits: Diminuição drástica da faixa dinâmica e aumento perceptível do ruído de quantização. O áudio soará 'granulado' ou distorcido, especialmente em partes mais silenciosas, e a transição entre diferentes volumes será menos suave.")
print("Em resumo, a qualidade do som será severamente degradada, soando abafado e com muito ruído.")

# 3. Calcular o tamanho teórico da parte de dados do áudio em bytes.
# A duração do áudio original foi calculada anteriormente e armazenada na variável 'duration'.
# duration = len(audio_data_original) / original_rate  (calculated previously)

target_rate_c = 4000  # Hz
bits_per_sample_c = 4
bytes_per_sample_c = bits_per_sample_c / 8

theoretical_size_bytes_c = duration * target_rate_c * bytes_per_sample_c
print(f"\niii) O tamanho teórico da parte de dados do áudio com uma taxa de amostragem de {target_rate_c} Hz e {bits_per_sample_c} bits é: {theoretical_size_bytes_c} bytes")

# 4. Analisar o código da função process_audio_advanced para verificar como o áudio com 4 bits é processado e salvo.
# Analyzing the process_audio_advanced function, specifically the 'if bits == 4:' block:
# audio_processed = np.round(audio_normalized * 7)  # values from -7 to +7 (15 levels)
# audio_processed = audio_processed + 7             # Rescale to [0, 14]
# audio_processed = np.uint8(audio_processed * (255 // 14)) # Map to [0, 255] using uint8
print("\niv) Análise do código para 4 bits:")
print("No bloco 'if bits == 4:', o áudio é quantizado para 15 níveis (correspondendo a aproximadamente 4 bits).")
print("No entanto, antes de salvar, os valores são mapeados para o intervalo [0, 255] e convertidos para o tipo de dado `np.uint8`.")
print("A função `wavfile.write` salva arrays `np.uint8` como áudio PCM de 8 bits sem sinal.")
print("Portanto, o arquivo WAV gerado NÃO mantém 4 bits por amostra; ele é salvo como um arquivo de áudio de 8 bits por amostra, onde os valores de 4 bits originais foram expandidos para caber na faixa de 8 bits.")

i) A maior frequência de Nyquist possível com uma taxa de amostragem de 4000 Hz é: 2000.0 Hz

ii) Efeito esperado na qualidade do som:
- Redução da taxa de amostragem para 4000 Hz: Perda significativa de frequências acima da frequência de Nyquist (2000.0 Hz). O som ficará muito abafado e sem clareza, especialmente para sons com conteúdo de alta frequência.
- Redução da profundidade de bits para 4 bits: Diminuição drástica da faixa dinâmica e aumento perceptível do ruído de quantização. O áudio soará 'granulado' ou distorcido, especialmente em partes mais silenciosas, e a transição entre diferentes volumes será menos suave.
Em resumo, a qualidade do som será severamente degradada, soando abafado e com muito ruído.

iii) O tamanho teórico da parte de dados do áudio com uma taxa de amostragem de 4000 Hz e 4 bits é: 60000.0 bytes

iv) Análise do código para 4 bits:
No bloco 'if bits == 4:', o áudio é quantizado para 15 níveis (correspondendo a aproximadamente 4 bits).
No entanto, antes de 

## Summary:

### Q&A

**A) i) What is the highest sound frequency in the file?**
Based on the visual inspection of the frequency spectrum plot, the highest significant frequency component appears to be around 18000 Hz.

**A) ii) Indicate the largest possible frequency component (in Hertz) when these digitization parameters are used.**
The largest possible frequency component is the Nyquist frequency, which for a sampling rate of 40kHz is 20000 Hz.

**A) iii) What is the theoretical size of the audio (data part)?**
The theoretical size of the audio data part with a 40kHz sampling rate and 16 bits per sample is 2,400,000 bytes.

**A) iv) The file size in bytes (see file properties, or Linux use the command "ls -l audio.wav") and indicate the reason for the difference between this size and the one calculated in iii).**
The file size using `ls -l` was 2,400,044 bytes. The difference between this size and the theoretical data size (2,400,000 bytes) is due to the WAV file header, which contains metadata about the audio.

**A) v) The file size on disk in bytes, observing the file properties, or in linux use "du -s -B1 audio.wav", and indicate the reason for the difference between this size and the file size in ii).**
The file size on disk using `du -s -B1` was 2,400,256 bytes. This is larger than the size reported by `ls -l` because file systems allocate disk space in fixed-size blocks. The file occupies at least one full block, and any unused space in the last block contributes to the on-disk size. (Note: The question asks for the difference between this size and the size in A) ii), which is the Nyquist frequency (20000 Hz). This seems to be a typo in the question; the comparison should be with the theoretical size or the `ls -l` size).

**A) vi) Indicate the size of this file on disk if your HD were formatted for a block size (disk allocation unit) of 2048 B.**
Assuming the file size from `ls -l` is 2,400,044 bytes, the size on disk with a block size of 2048 B would be 2,402,304 bytes.

**B) i) What effect occurred with this change in sampling rate? What is the highest possible sound frequency with these digitization parameters?**
Lowering the sampling rate to 10kHz removes frequencies above the Nyquist frequency (5000 Hz), resulting in a muffled sound. The highest possible sound frequency with a 10kHz sampling rate is 5000 Hz.

**B) ii) What is the size in bytes of the audio data part after this conversion?**
The theoretical size of the audio data part with a 10kHz sampling rate and 16 bits per sample is 600,000 bytes.

**C) i) What effect occurred with this change in sampling rate? What is the highest possible sound frequency with these digitization parameters?**
Lowering the sampling rate to 4kHz removes frequencies above the Nyquist frequency (2000 Hz), making the sound very muffled. The highest possible sound frequency with a 4kHz sampling rate is 2000 Hz.

**C) ii) What is the theoretical size in bytes of the audio data part after this conversion?**
The theoretical size of the audio data part with a 4kHz sampling rate and 4 bits per sample is 60,000 bytes.

**C) iii) Does the audio file generated in the notebook maintain 4 bits per sample in the file?**
No, the audio file generated does not maintain 4 bits per sample. Although the audio is quantized to 4 bits, it is saved as an 8-bit audio file where the original 4-bit values have been expanded to fit the 8-bit range.

### Data Analysis Key Findings

*   The original audio file contains significant frequencies up to approximately 18000 Hz.
*   The Nyquist frequency is directly half of the sampling rate (20000 Hz for 40kHz, 5000 Hz for 10kHz, and 2000 Hz for 4kHz).
*   Reducing the sampling rate removes audio frequencies above the Nyquist frequency, leading to a loss of clarity and a muffled sound (more pronounced at lower sampling rates like 10kHz and 4kHz).
*   Reducing the bit depth significantly increases quantization noise and decreases dynamic range, resulting in a distorted or "grainy" sound (severely degraded at 4 bits per sample).
*   The theoretical size of the audio data is proportional to the duration, sampling rate, and bits per sample.
*   The actual WAV file size is larger than the theoretical data size due to the file header.
*   The file size on disk is larger than the actual file size due to file system block allocation.
*   The provided processing code for 4-bit audio saves the output as an 8-bit WAV file by mapping the 4-bit values to an 8-bit range.

### Insights or Next Steps

*   Lowering sampling rate and bit depth significantly degrades audio quality but reduces file size, illustrating the trade-off in audio compression.
*   Understanding file system block allocation is crucial for predicting the actual disk space consumed by files, which is often larger than the reported file size.


In [26]:
# A) Alterar o som para manter os parâmetros próximos do original: 40kHz e 16 bits por amostra.
from scipy.io import wavfile
import numpy as np

# Execute a célula anterior (MGAPfz0VI84G) e ajuste os widgets para:
# Sampling Rate: 40000
# Bits per Sample: 16

# i) Qual é a maior frequência de som no arquivo?
# ii) Indique o maior componente de frequência (em Hertz) possível quando estes parâmetros de digitalização são utilizados.
# iii) Qual é o tamanho teórico do áudio (parte de dados);
# iv) O tamanho do arquivo em bytes (ver propriedades do arquivo, ou Linux utilize o comando "ls -l audio.wav) e indique o motivo da diferença entre este tamanho e o calculado em ii).

# Para responder i), ii), iii) e iv), vamos ler o arquivo original e calcular algumas propriedades.

original_rate, audio_data = wavfile.read("audio.wav")

# i) A maior frequência de som no arquivo original is limited by the original sampling rate.
# According to the Nyquist theorem, the maximum frequency that can be captured is half of the sampling rate.
max_freq_original = original_rate / 2
print(f"i) Maior frequência de som no arquivo original (Nyquist): {max_freq_original} Hz")

# ii) When the audio is digitized with a sampling rate of 40kHz, the maximum possible frequency is half of that rate.
max_freq_processed = 40000 / 2
print(f"ii) Maior componente de frequência possível com 40kHz de taxa de amostragem: {max_freq_processed} Hz")

# iii) The theoretical size of the audio (data part) can be calculated as:
# number of samples * number of channels * number of bytes per sample
# For 16 bits per sample, we have 2 bytes per sample.
num_samples_original = len(audio_data)
num_channels_original = 1 if len(audio_data.shape) == 1 else audio_data.shape[1]
bytes_per_sample_16bit = 16 / 8
tamanho_teorico_dados = num_samples_original * num_channels_original * bytes_per_sample_16bit
print(f"iii) Tamanho teórico da parte de dados do áudio original (16 bits/amostra): {tamanho_teorico_dados} bytes")


# iv) To answer this question, you will need to check the size of the "audio.wav" file
# using the file properties on your operating system or the `ls -l audio.wav` command in the terminal.
# The difference between the file size and the theoretical data size (calculated in iii))
# is due to the WAV file header, which contains metadata about the audio (such as sampling rate, number of channels, etc.).
print("iv) Para responder esta questão, verifique o tamanho do arquivo 'audio.wav' no seu sistema.")
print("A diferença para o tamanho teórico dos dados (calculado em iii)) é o tamanho do cabeçalho do arquivo WAV.")


# v) and vi) To answer these questions, you will need to check the size of the file on disk
# using the file properties or the `du -s -B1 audio.wav` command in the terminal.
# The size on disk is generally larger than the file size due to the block size
# (allocation unit) of the file system. The system allocates space in multiples of the block size.
print("v) Para responder esta questão, verifique o tamanho do arquivo em disco no seu sistema.")
print("A diferença para o tamanho do arquivo é devido ao tamanho do bloco do sistema de arquivos.")

# To answer vi), you will need to consider that the system allocates space in multiples of the block size.
# If the block size is 2048 B, the size on disk will be the smallest multiple of 2048 B that is greater than or equal to the file size.
print("vi) Para responder esta questão, calcule o menor múltiplo de 2048 B que seja maior ou igual ao tamanho do arquivo.")

FileNotFoundError: [Errno 2] No such file or directory: 'audio.wav'